In [1]:
import json
import pandas as pd
import os
import copy

In [2]:
files = os.listdir("./")
storage = []
for file in files:
    if file[-5:] == ".json":
        with open(file, mode="r", encoding="UTF-8") as file:
            storage.append(json.load(file))

In [3]:
!pip install docx
!pip install python-docx 
import docx


[notice] A new release of pip is available: 23.3.1 -> 23.3.2
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 23.3.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [4]:
storage[0][1]["annotations"]

[{'id': 377513,
  'completed_by': 123,
  'result': [{'id': 'YkACxk9cR-',
    'type': 'labels',
    'value': {'end': 34,
     'text': '27 лет',
     'start': 28,
     'labels': ['Личные параметры']},
    'origin': 'manual',
    'to_name': 'text',
    'from_name': 'label'},
   {'id': 'RI_K6VIQKG',
    'type': 'labels',
    'value': {'end': 47,
     'text': 'пол-женский',
     'start': 36,
     'labels': ['Личные параметры']},
    'origin': 'manual',
    'to_name': 'text',
    'from_name': 'label'},
   {'id': 'pJxzV2ussB',
    'type': 'labels',
    'value': {'end': 185,
     'text': 'Наблюдение до 12-ой недели в центре планирования семьи и репродукции. С 28-ой недели – в клинике акушерства мма им. И.м. сеченова',
     'start': 56,
     'labels': ['Анамнез']},
    'origin': 'manual',
    'to_name': 'text',
    'from_name': 'label'},
   {'id': 'twzHJQXy_o',
    'type': 'labels',
    'value': {'end': 459,
     'text': 'глюкозу',
     'start': 452,
     'labels': ['Лекарство']},
    'origin':

In [6]:
text_ls = []
start_ls = []
end_ls = []
labels_ls = []
steps = []
file_n = []
for test in storage:
    for i, history in enumerate(test):
        for val in history["annotations"][0]["result"]:
            text_ls.append(val["value"]["text"])
            start_ls.append(val["value"]["start"])
            end_ls.append(val["value"]["end"])
            file_n.append(i)
            for label in val["value"]["labels"]:
                labels_ls.append(label)
    steps.append(len(text_ls))

In [7]:
print(len(text_ls))
print(len(start_ls))
print(len(end_ls))
print(len(labels_ls))
print(len(file_n))

38867
38867
38867
38867
38867


In [8]:
df = pd.DataFrame(columns=["text", "label", "start", "end"])
df["text"] = text_ls
df["label"] = labels_ls
df["start"] = start_ls
df["end"] = end_ls
df["history"] = file_n

In [9]:
new_col = []
j = 0
for i in range(len(df)):
    if i >= steps[j]:
        j += 1
    new_col.append(j)

df["file"] = new_col

In [10]:
df.where((df["history"] == 0) & (df["file"] == 0)).sort_values("start").dropna()

text             label   start     end  history  \
1                       19 лет  Личные параметры    34.0    40.0      0.0   
2                      мужской  Личные параметры    47.0    54.0      0.0   
3                      русский  Личные параметры    72.0    79.0      0.0   
0            1 марта 2006 года  Личные параметры   109.0   126.0      0.0   
93                затрудненное           Оттенок   180.0   192.0      0.0   
..                         ...               ...     ...     ...      ...   
109                          1        Количество  3693.0  3694.0      0.0   
112                      0,1 г          Значение  3702.0  3707.0      0.0   
103                          2        Количество  3709.0  3710.0      0.0   
102  тетерациклина гидрохлорид         Лекарство  3726.0  3751.0      0.0   
104                          3        Количество  3776.0  3777.0      0.0   

     file  
1     0.0  
2     0.0  
3     0.0  
0     0.0  
93    0.0  
..    ...  
109   0.0  
112   0.0  
103   0.0  
102   0.0  
104   0.0  

[118 rows x 6 columns]

In [16]:
df["label"].value_counts()

Значение             12033
Анамнез               8500
Симптомы              3784
Анализ                2573
Лекарство             2180
Болезнь               1912
Дата                  1847
Лечение               1457
Количество            1315
Оттенок               1306
Личные параметры       772
Продолжительность      557
Место                  369
Время                  262
Name: label, dtype: int64

In [46]:
files = ["./История болезни 1-50.docx", "./История болезни 51-100.docx",
        "./История болезни 101-150.docx", "./История болезни 151-200.docx",
        "./История болезни 201-250.docx"]

In [233]:
out = []
all_files = []
for f in files:
    doc = docx.Document(f)
    fullText = ""
    c = len("История болезни ")  #16
    for para in doc.paragraphs:
        fullText += para.text
        fullText += "\n"
    hists = fullText.split("История болезни ")[1:]
    all_files.append(hists)

In [234]:
for file_idx in range(5):
    for hist_idx in range(50):
        tmp = df.where((df["history"] == hist_idx) & (df["file"] == file_idx)).sort_values("start").dropna()
        before = 0
        for i, value in enumerate(tmp.values):
            start = int(value[2])
            end = int(value[3])
            hist = int(value[4])
            file_ = int(value[5])
            ff = all_files[file_]
            if i == 0:
                out.append(ff[hist][3:start-c])
            else:
                out.append(ff[hist][before:start-c])
            before = end - c + 1

In [235]:
signs = ["", " ", ".", ";", "\n", "(", ")", "\n.", ", ", "\n. ", " \n"]

for s in signs:
    while s in out:
        out.remove(s)

In [236]:
cp = copy.deepcopy(out)
for s in cp:
    if len(s) <= 2:
        out.remove(s)

In [239]:
len(out)

19090

In [237]:
big_df = copy.deepcopy(df)
for text in out:
    correct = text.replace("\n", "")
    ex = {"text": correct,
          "label": "Лишнее",
          "start": 0.0,
          "end": 0.0,
          "history": -1,
          "file": -1}
    big_df = big_df.append(ex, ignore_index=True)

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

...

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\Users\chern\AppData\Local\Temp\ipykernel_18112\3750542714.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  big_df = big_df.append(ex, ignore_index=True)
C:\U

In [238]:
big_df

text             label  \
0                                      1 марта 2006 года  Личные параметры   
1                                                 19 лет  Личные параметры   
2                                                мужской  Личные параметры   
3                                                русский  Личные параметры   
4                           затрудненное носовое дыхание          Симптомы   
...                                                  ...               ...   
57952  цвета. Десны розовые, чистые, обычной влажност...            Лишнее   
57953   пластинчатыми чешуйками. При поскабливании па...            Лишнее   
57954  чешуйками. В начальной стадии заболевания крае...            Лишнее   
57955                                       ( препараты             Лишнее   
57956                               . Наружная терапия:             Лишнее   

       start    end  history  file  
0      109.0  126.0        0     0  
1       34.0   40.0        0     0  
2       47.0   54.0        0     0  
3       72.0   79.0        0     0  
4      180.0  208.0        0     0  
...      ...    ...      ...   ...  
57952    0.0    0.0       -1    -1  
57953    0.0    0.0       -1    -1  
57954    0.0    0.0       -1    -1  
57955    0.0    0.0       -1    -1  
57956    0.0    0.0       -1    -1  

[57957 rows x 6 columns]

In [240]:
big_df.to_csv("./full_data.csv", index=None)